In [9]:
import os
import warnings
from pathlib import Path
from IPython.display import clear_output
from IPython.display import display
from pandas.api.types import CategoricalDtype

# Basic libraries
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import seaborn as sns

# Clustering
from sklearn.cluster import KMeans

# Plotly
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.figure_factory as ff
import plotly.offline as offline
import plotly.graph_objs as go

def load_ionosphere():
    data_dir = Path("Archivos_CSV")
    df1 = pd.read_csv(data_dir / "ionosphere_1NN")
    df2 = pd.read_csv(data_dir / "ionosphere_GR")
    df3 = pd.read_csv(data_dir / "ionosphere_LS")
    df4 = pd.read_csv(data_dir / "ionosphere_AGGBLX")
    df5 = pd.read_csv(data_dir / "ionosphere_AGGAC")
    df6 = pd.read_csv(data_dir / "ionosphere_AGEBLX")
    df7 = pd.read_csv(data_dir / "ionosphere_AGEAC")
    df8 = pd.read_csv(data_dir / "ionosphere_AM1")
    df9 = pd.read_csv(data_dir / "ionosphere_AM2")
    df10 = pd.read_csv(data_dir / "ionosphere_AM3")
    
    df11 = pd.read_csv(data_dir / "ionosphere_BBBC")
    df12 = pd.read_csv(data_dir / "ionosphere_BBBC+LocalSearch")

    
    # Merge the splits so we can process them together
    df = pd.concat([df1, df2, df3, df4, df5, df6, df7, df8, df9, df10, df11, df12], axis=0)
    return df

def load_parkinsons():
    data_dir = Path("Archivos_CSV")
    df1 = pd.read_csv(data_dir / "parkinson_1NN")
    df2 = pd.read_csv(data_dir / "parkinson_GR")
    df3 = pd.read_csv(data_dir / "parkinson_LS")
    df4 = pd.read_csv(data_dir / "parkinson_AGGBLX")
    df5 = pd.read_csv(data_dir / "parkinson_AGGAC")
    df6 = pd.read_csv(data_dir / "parkinson_AGEBLX")
    df7 = pd.read_csv(data_dir / "parkinson_AGEAC")
    df8 = pd.read_csv(data_dir / "parkinson_AM1")
    df9 = pd.read_csv(data_dir / "parkinson_AM2")
    df10 = pd.read_csv(data_dir / "parkinson_AM3")
    
    df11 = pd.read_csv(data_dir / "parkinson_BBBC")
    df12 = pd.read_csv(data_dir / "parkinson_BBBC+LocalSearch")
    # Merge the splits so we can process them together
    df = pd.concat([df1, df2, df3, df4, df5, df6, df7, df8, df9, df10, df11, df12], axis=0)
    return df

def load_spectf_heart():
    data_dir = Path("Archivos_CSV")
    df1 = pd.read_csv(data_dir / "heartspectf_1NN")
    df2 = pd.read_csv(data_dir / "heartspectf_GR")
    df3 = pd.read_csv(data_dir / "heartspectf_LS")
    df4 = pd.read_csv(data_dir / "heartspectf_AGGBLX")
    df5 = pd.read_csv(data_dir / "heartspectf_AGGAC")
    df6 = pd.read_csv(data_dir / "heartspectf_AGEBLX")
    df7 = pd.read_csv(data_dir / "heartspectf_AGEAC")
    df8 = pd.read_csv(data_dir / "heartspectf_AM1")
    df9 = pd.read_csv(data_dir / "heartspectf_AM2")
    df10 = pd.read_csv(data_dir / "heartspectf_AM3")
    
    df11 = pd.read_csv(data_dir / "heartspectf_BBBC")
    df12 = pd.read_csv(data_dir / "heartspectf_BBBC+LocalSearch")
    # Merge the splits so we can process them together
    df = pd.concat([df1, df2, df3, df4, df5, df6, df7, df8, df9, df10, df11, df12], axis=0)
    return df

clear_output()

In [10]:
ionosphere = load_ionosphere()
parkinsons = load_parkinsons()
spectf_heart = load_spectf_heart()
ionosphere.columns = ['Particion','T_Clas','T_Red','Agr','Tiempo','Algoritmo']
parkinsons.columns = ['Particion','T_Clas','T_Red','Agr','Tiempo','Algoritmo']
spectf_heart.columns = ['Particion','T_Clas','T_Red','Agr','Tiempo','Algoritmo']

# Analisis de tiempos

In [11]:
"""
function annotation_helper(...)

Helper for annotations in plotly. While reducing the amount of code to create an annotation, it also:
- Allows us to provide the text into an array of 
  strings(one for each new line) instead of one really long <br> separated text param
- Provides basic functionality for individual line spacing(s) between each line
- Custom annotation rectangle
- Basic debugging for annotation positioning
"""

def annotation_helper(fig, texts, x, y, line_spacing, align="left", bgcolor="rgba(0,0,0,0)", borderpad=0, ref="axes", xref="x", yref="y", width=100, debug = False):
    
    is_line_spacing_list = isinstance(line_spacing, list)
    total_spacing = 0
    
    for index, text in enumerate(texts):
        if is_line_spacing_list and index!= len(line_spacing):
            current_line_spacing = line_spacing[index]
        elif not is_line_spacing_list:
            current_line_spacing = line_spacing
        
        fig.add_annotation(dict(
            x= x,
            y= y - total_spacing,
            width = width,
            showarrow=False,
            text= text,
            align= align,
            borderpad=4 if debug == False else 0, # doesn't work with new background box implementation :S
            xref= "paper" if ref=="paper" else xref,
            yref= "paper" if ref=="paper" else yref,
            
            bordercolor= "#222",
            borderwidth= 2 if debug == True else 0 # shows the actual borders of the annotation box
        ))
        
        total_spacing  += current_line_spacing
    
    if bgcolor != "rgba(0,0,0,0)":
        fig.add_shape(type="rect",
            xref= "paper" if ref=="paper" else xref,
            yref= "paper" if ref=="paper" else yref,
            xanchor = x, xsizemode = "pixel", 
            x0=-width/2, x1= +width/2, y0=y + line_spacing[-1], y1=y -total_spacing,
            fillcolor= bgcolor,
            line = dict(width=0))  
      
    if debug == True:
        handle_annot_debug(fig, x, y, ref)

fig = make_subplots(rows=1, cols=1)        
        
fig.add_trace(go.Bar(x=ionosphere[ionosphere.Particion <= 4]['Algoritmo'], y=ionosphere[ionosphere.Particion <= 4]['Tiempo'], name='Ionosphere'), row = 1, col = 1)
fig.add_trace(go.Bar(x=parkinsons[parkinsons.Particion <= 4]['Algoritmo'], y=parkinsons[parkinsons.Particion <= 4]['Tiempo'], name='Parkinson'), row = 1, col = 1)
fig.add_trace(go.Bar(x=spectf_heart[spectf_heart.Particion <= 4]['Algoritmo'], y=spectf_heart[spectf_heart.Particion <= 4]['Tiempo'], name='Spectf-Heart'), row = 1, col = 1)

fig.update_xaxes(visible = True, row=1, col=1)
fig.update_layout(legend = dict(bgcolor = 'rgb(242,242,242)'))
# General Styling
fig.update_layout(height=400, bargap=0.2,
                  margin=dict(b=50,r=30,l=100),
                  plot_bgcolor='rgb(242,242,242)',
                  #paper_bgcolor = 'rgb(242,242,242)',
                  font=dict(family="Times New Roman", size= 14),
                  hoverlabel=dict(font_color="floralwhite"),
                  showlegend=True)

#Title
text = [
    "<span style='font-size:35px; font-family:Times New Roman'>Análisis de tiempos entre Algoritmos y Datasets</span>"
]
annotation_helper(fig, text, -0.043, 1.4, [0.095,0.095,0.065],ref="paper", width=1300)
#Subtitle
text = [
    "<span style='font-size:14px; font-family:Helvetica'> Análisis de los tiempos de ejecución obtenidos para cada uno de los algoritmos. Además, hemos diferenciado por datasets con el fin de realizar una mejor comparativa. La barra en </span>",
    "<span style='font-size:14px; font-family:Helvetica'> su totalidad representa el tiempo total. Por su parte, cada trozo representa el tiempo en cada una de las 5 particiones. </span>",
]
annotation_helper(fig, text, -0.043, 1.225, [0.065,0.05,0.065],ref="paper", width=1300)
fig.show()

# Analisis de tiempos

In [12]:
fig = make_subplots(rows=1, cols=1)        
        
fig.add_trace(go.Box(x=ionosphere[ionosphere.Particion <= 4]['Algoritmo'], y=ionosphere[ionosphere.Particion <= 4]['T_Clas'], name='Ionosphere'), row = 1, col = 1)
fig.add_trace(go.Box(x=parkinsons[parkinsons.Particion <= 4]['Algoritmo'], y=parkinsons[parkinsons.Particion <= 4]['T_Clas'], name='Parkinson'), row = 1, col = 1)
fig.add_trace(go.Box(x=spectf_heart[spectf_heart.Particion <= 4]['Algoritmo'], y=spectf_heart[spectf_heart.Particion <= 4]['T_Clas'], name='Spectf-Heart'), row = 1, col = 1)

fig.update_xaxes(visible = True, row=1, col=1)
fig.update_layout(legend = dict(bgcolor = 'rgb(242,242,242)'))
# General Styling
fig.update_layout(height=400, bargap=0.2,
                  margin=dict(b=50,r=30,l=100),
                  plot_bgcolor='rgb(242,242,242)',
                  #paper_bgcolor = 'rgb(242,242,242)',
                  font=dict(family="Times New Roman", size= 14),
                  hoverlabel=dict(font_color="floralwhite"),
                  showlegend=True)

#Title
text = [
    "<span style='font-size:35px; font-family:Times New Roman'>Análisis de la tasa de clasificación entre Datasets</span>"
]
annotation_helper(fig, text, -0.043, 1.4, [0.095,0.095,0.065],ref="paper", width=1300)
#Subtitle
text = [
    "<span style='font-size:14px; font-family:Helvetica'> Análisis de los valores obtenidos para la tasa de clasificación, para cada uno de los algoritmos. Además, hemos diferenciado por datasets con el fin de realizar una mejor comparativa. </span>"
]
annotation_helper(fig, text, -0.043, 1.225, [0.065,0.05,0.065],ref="paper", width=1300)
fig.show()

In [13]:
fig = make_subplots(rows=1, cols=3)        
        
fig.add_trace(go.Box(x=ionosphere[ionosphere.Particion <= 4]['Algoritmo'], y=ionosphere[ionosphere.Particion <= 4]['T_Clas'], name='Ionosphere'), row = 1, col = 1)
fig.add_trace(go.Box(x=parkinsons[parkinsons.Particion <= 4]['Algoritmo'], y=parkinsons[parkinsons.Particion <= 4]['T_Clas'], name='Parkinson'), row = 1, col = 2)
fig.add_trace(go.Box(x=spectf_heart[spectf_heart.Particion <= 4]['Algoritmo'], y=spectf_heart[spectf_heart.Particion <= 4]['T_Clas'], name='Spectf-Heart'), row = 1, col = 3)

fig.update_xaxes(visible = True, row=1, col=1)
fig.update_layout(legend = dict(bgcolor = 'rgb(242,242,242)'))
# General Styling
fig.update_layout(height=400, bargap=0.2,
                  margin=dict(b=50,r=30,l=100),
                  plot_bgcolor='rgb(242,242,242)',
                  #paper_bgcolor = 'rgb(242,242,242)',
                  font=dict(family="Times New Roman", size= 14),
                  hoverlabel=dict(font_color="floralwhite"),
                  showlegend=True)

#Title
text = [
    "<span style='font-size:35px; font-family:Times New Roman'>Análisis de la tasa de clasificación entre Algoritmos</span>"
]
annotation_helper(fig, text, -0.043, 1.4, [0.095,0.095,0.065],ref="paper", width=1300)
#Subtitle
text = [
    "<span style='font-size:14px; font-family:Helvetica'> Análisis de los valores obtenidos para la tasa de clasificación, para cada uno de los algoritmos. Además, hemos diferenciado por datasets con el fin de realizar una mejor comparativa. </span>"
]
annotation_helper(fig, text, -0.043, 1.225, [0.065,0.05,0.065],ref="paper", width=1300)
fig.show()

# Analisis Tasa Reduccion

In [14]:
fig = make_subplots(rows=1, cols=1)        
        
fig.add_trace(go.Bar(x=ionosphere[ionosphere.Particion == 5]['Algoritmo'], y=ionosphere[ionosphere.Particion == 5]['T_Red'], name='Ionosphere'), row = 1, col = 1)
fig.add_trace(go.Bar(x=parkinsons[parkinsons.Particion == 5]['Algoritmo'], y=parkinsons[parkinsons.Particion == 5]['T_Red'], name='Parkinson'), row = 1, col = 1)
fig.add_trace(go.Bar(x=spectf_heart[spectf_heart.Particion == 5]['Algoritmo'], y=spectf_heart[spectf_heart.Particion == 5]['T_Red'], name='Spectf-Heart'), row = 1, col = 1)

fig.update_xaxes(visible = True, row=1, col=1)
fig.update_layout(legend = dict(bgcolor = 'rgb(242,242,242)'))
# General Styling
fig.update_layout(height=400, bargap=0.2,
                  margin=dict(b=50,r=30,l=100),
                  plot_bgcolor='rgb(242,242,242)',
                  #paper_bgcolor = 'rgb(242,242,242)',
                  font=dict(family="Times New Roman", size= 14),
                  hoverlabel=dict(font_color="floralwhite"),
                  showlegend=True)

#Title
text = [
    "<span style='font-size:35px; font-family:Times New Roman'>Análisis de la tasa de reducción entre Algoritmos y Datasets</span>"
]
annotation_helper(fig, text, -0.043, 1.4, [0.095,0.095,0.065],ref="paper", width=1300)
#Subtitle
text = [
    "<span style='font-size:14px; font-family:Helvetica'> Análisis de los valores obtenidos para la tasa de reducción, de cada uno de los algoritmos. Además, hemos diferenciado por datasets con el fin de realizar una mejor comparativa. </span>"
]
annotation_helper(fig, text, -0.043, 1.225, [0.065,0.05,0.065],ref="paper", width=1300)
fig.show()

# Analisis funcion objetivo

In [15]:
media_ionosphere = ionosphere[ionosphere.Particion == 5]
media_parkinsons = parkinsons[parkinsons.Particion == 5]
media_spectf_heart = spectf_heart[spectf_heart.Particion == 5]


fig = make_subplots(rows=1, cols=1)        
        
fig.add_trace(go.Bar(x=media_ionosphere['Algoritmo'], y=media_ionosphere['Agr'], name='Ionosphere'), row = 1, col = 1)
fig.add_trace(go.Bar(x=media_parkinsons['Algoritmo'], y=media_parkinsons['Agr'], name='Parkinson'), row = 1, col = 1)
fig.add_trace(go.Bar(x=media_spectf_heart['Algoritmo'], y=media_spectf_heart['Agr'], name='Spectf-Heart'), row = 1, col = 1)

fig.add_hline(y=0.8857)
fig.update_xaxes(visible = True, row=1, col=1)
fig.update_layout(legend = dict(bgcolor = 'rgb(242,242,242)'))
# General Styling
fig.update_layout(height=400, bargap=0.2,
                  margin=dict(b=50,r=30,l=100),
                  plot_bgcolor='rgb(242,242,242)',
                  #paper_bgcolor = 'rgb(242,242,242)',
                  font=dict(family="Times New Roman", size= 14),
                  hoverlabel=dict(font_color="floralwhite"),
                  showlegend=True)

#Title
text = [
    "<span style='font-size:35px; font-family:Times New Roman'>Análisis de la función objetivo entre Algoritmos y Datasets</span>"
]
annotation_helper(fig, text, -0.043, 1.4, [0.095,0.095,0.065],ref="paper", width=1300)
#Subtitle
text = [
    "<span style='font-size:14px; font-family:Helvetica'> Análisis de los valores promedios obtenidos para la función objetivo de cada algoritmo. Además, hemos diferenciado por cada uno de los datasets para poder realizar así una </span>",
    "<span style='font-size:14px; font-family:Helvetica'> mejor comparativa. </span>",
]
annotation_helper(fig, text, -0.043, 1.225, [0.065,0.05,0.065],ref="paper", width=1300)

fig.show()

# Convergencia

In [13]:
fig = make_subplots(rows=1, cols=2, column_widths=[0.5, 0.5], vertical_spacing=0.1, horizontal_spacing=0.1,
                    subplot_titles=('Big Bang - Big Crunch','Big Bang - Big Crunch + Local Search))

# ============== AGGAC ===================

io_AGGAC_1 = [0.6157563025210084, 0.6157563025210084, 0.6157563025210084, 0.6175420168067227, 0.6175420168067227, 0.6175420168067227, 0.6175420168067227, 0.6175420168067227, 0.6175420168067227, 0.626890756302521, 0.626890756302521, 0.626890756302521, 0.626890756302521, 0.626890756302521, 0.626890756302521, 0.6451680672268907, 0.6451680672268907, 0.6451680672268907, 0.6451680672268907, 0.6451680672268907, 0.6451680672268907, 0.6451680672268907, 0.6451680672268907, 0.6451680672268907, 0.6451680672268907, 0.646953781512605, 0.646953781512605, 0.646953781512605, 0.646953781512605, 0.6505252100840335, 0.6505252100840335, 0.6670168067226891, 0.6670168067226891, 0.6670168067226891, 0.6670168067226891, 0.6670168067226891, 0.6688025210084034, 0.6688025210084034, 0.6688025210084034, 0.6688025210084034, 0.6688025210084034, 0.6688025210084034, 0.6688025210084034, 0.6688025210084034, 0.6688025210084034, 0.679936974789916, 0.679936974789916, 0.679936974789916, 0.679936974789916, 0.679936974789916, 0.6852941176470588, 0.6852941176470588, 0.6852941176470588, 0.6852941176470588, 0.6852941176470588, 0.6852941176470588, 0.6852941176470588, 0.6852941176470588, 0.6852941176470588, 0.6852941176470588, 0.6852941176470588, 0.6852941176470588, 0.6852941176470588, 0.6852941176470588, 0.6852941176470588, 0.6852941176470588, 0.6852941176470588, 0.6870798319327731, 0.6870798319327731, 0.6870798319327731, 0.6870798319327731, 0.6870798319327731, 0.6870798319327731, 0.6870798319327731, 0.6870798319327731, 0.6888655462184874, 0.6888655462184874, 0.6906512605042017, 0.6906512605042017, 0.6906512605042017, 0.6906512605042017, 0.6906512605042017, 0.6906512605042017, 0.6906512605042017, 0.6906512605042017, 0.6906512605042017, 0.6906512605042017, 0.6906512605042017, 0.6906512605042017, 0.6906512605042017, 0.6906512605042017, 0.6906512605042017, 0.6906512605042017, 0.6906512605042017, 0.6906512605042017, 0.6906512605042017, 0.6906512605042017, 0.6946428571428571, 0.6946428571428571, 0.6946428571428571, 0.6946428571428571, 0.6946428571428571, 0.6946428571428571, 0.6946428571428571, 0.6946428571428571, 0.6946428571428571, 0.6946428571428571, 0.6946428571428571, 0.7071428571428571, 0.7071428571428571, 0.7071428571428571, 0.7071428571428571, 0.7071428571428571, 0.7071428571428571, 0.7071428571428571, 0.7071428571428571, 0.7071428571428571, 0.7071428571428571, 0.7071428571428571, 0.7071428571428571, 0.7071428571428571, 0.7089285714285714, 0.7089285714285714, 0.7089285714285714, 0.7089285714285714, 0.7089285714285714, 0.7089285714285714, 0.7089285714285714, 0.7089285714285714, 0.7089285714285714, 0.7089285714285714, 0.7089285714285714, 0.7218487394957983, 0.7218487394957983, 0.7218487394957983, 0.7218487394957983, 0.7218487394957983, 0.7218487394957983, 0.7218487394957983, 0.7218487394957983, 0.7218487394957983, 0.7218487394957983, 0.7218487394957983, 0.7218487394957983, 0.7218487394957983, 0.7218487394957983, 0.7218487394957983, 0.7218487394957983, 0.7218487394957983, 0.7218487394957983, 0.7218487394957983, 0.7218487394957983, 0.7218487394957983, 0.7218487394957983, 0.7218487394957983, 0.7218487394957983, 0.7218487394957983, 0.7347689075630253, 0.7347689075630253, 0.7347689075630253, 0.7347689075630253, 0.7347689075630253, 0.7347689075630253, 0.7347689075630253, 0.7347689075630253, 0.7347689075630253, 0.7347689075630253, 0.7347689075630253, 0.7347689075630253, 0.7347689075630253, 0.7347689075630253, 0.7347689075630253, 0.7347689075630253, 0.7347689075630253, 0.7347689075630253, 0.7365546218487395, 0.7365546218487395, 0.7365546218487395, 0.7365546218487395, 0.7365546218487395, 0.7365546218487395, 0.7365546218487395, 0.7365546218487395, 0.7365546218487395, 0.7365546218487395, 0.7365546218487395, 0.7365546218487395, 0.7365546218487395, 0.7365546218487395, 0.7383403361344538, 0.7383403361344538, 0.7383403361344538, 0.7401260504201681, 0.7401260504201681, 0.7401260504201681, 0.7441176470588236, 0.7441176470588236, 0.7441176470588236, 0.7441176470588236, 0.7441176470588236, 0.7441176470588236, 0.7441176470588236, 0.7441176470588236, 0.7441176470588236, 0.7441176470588236, 0.7441176470588236, 0.7441176470588236, 0.7441176470588236, 0.7441176470588236, 0.7441176470588236, 0.7441176470588236, 0.7441176470588236, 0.7441176470588236, 0.7441176470588236, 0.7441176470588236, 0.7441176470588236, 0.7494747899159664, 0.7494747899159664, 0.7494747899159664, 0.7494747899159664, 0.7494747899159664, 0.7494747899159664, 0.7494747899159664, 0.7494747899159664, 0.7494747899159664, 0.7494747899159664, 0.7494747899159664, 0.7494747899159664, 0.7494747899159664, 0.7494747899159664, 0.7494747899159664, 0.7494747899159664, 0.7494747899159664, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7512605042016807, 0.7623949579831932, 0.7623949579831932, 0.7623949579831932, 0.7623949579831932, 0.7623949579831932, 0.7623949579831932, 0.7623949579831932, 0.7623949579831932, 0.7623949579831932, 0.7623949579831932, 0.7623949579831932, 0.7641806722689075, 0.7641806722689075, 0.7641806722689075, 0.7641806722689075, 0.7641806722689075, 0.7641806722689075, 0.7659663865546218, 0.7659663865546218, 0.7659663865546218, 0.7659663865546218, 0.7659663865546218, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647, 0.7713235294117647]
tam = [i for i in range(len(io_AGGAC_1))]
fig.add_trace(go.Scatter(y=io_AGGAC_1, x=tam, name='Partición 1', marker = dict(color = 'lightblue')), row=1, col=1)

io_AGGAC_2 = [0.6471634917312121, 0.6471634917312121, 0.6471634917312121, 0.6471634917312121, 0.6471634917312121, 0.6471634917312121, 0.6471634917312121, 0.6471634917312121, 0.6471634917312121, 0.6471634917312121, 0.6471634917312121, 0.6471634917312121, 0.6471634917312121, 0.6471634917312121, 0.6471634917312121, 0.6471634917312121, 0.6471634917312121, 0.6471634917312121, 0.6471634917312121, 0.6471634917312121, 0.6471634917312121, 0.6471634917312121, 0.648942851161817, 0.6583106552229432, 0.6600900146535482, 0.6600900146535482, 0.6600900146535482, 0.6600900146535482, 0.6618693740841533, 0.6618693740841533, 0.6747958970064893, 0.6747958970064893, 0.6747958970064893, 0.6747958970064893, 0.6747958970064893, 0.6747958970064893, 0.6747958970064893, 0.6747958970064893, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6930604982206405, 0.6930604982206405, 0.6930604982206405, 0.6930604982206405, 0.6930604982206405, 0.6930604982206405, 0.6930604982206405, 0.6930604982206405, 0.6930604982206405, 0.6930604982206405, 0.6930604982206405, 0.6930604982206405, 0.6930604982206405, 0.7059870211429768, 0.7059870211429768, 0.7059870211429768, 0.7059870211429768, 0.7059870211429768, 0.7059870211429768, 0.7059870211429768, 0.7059870211429768, 0.7059870211429768, 0.7059870211429768, 0.7059870211429768, 0.7059870211429768, 0.7059870211429768, 0.7059870211429768, 0.7059870211429768, 0.7059870211429768, 0.7059870211429768, 0.7059870211429768, 0.7059870211429768, 0.7059870211429768, 0.7059870211429768, 0.7059870211429768, 0.7095457400041867, 0.7095457400041867, 0.7095457400041867, 0.7095457400041867, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.720692903495918, 0.720692903495918, 0.720692903495918, 0.720692903495918, 0.720692903495918, 0.720692903495918, 0.722472262926523, 0.722472262926523, 0.722472262926523, 0.722472262926523, 0.7242516223571279, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7278103412183379, 0.7278103412183379, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7389575047100692, 0.7501046682018003, 0.7518840276324052, 0.7518840276324052, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7630311911241365, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.7683692694159514, 0.7683692694159514, 0.7683692694159514, 0.7683692694159514, 0.7683692694159514, 0.7683692694159514, 0.7683692694159514, 0.7683692694159514, 0.7683692694159514, 0.7683692694159514, 0.7683692694159514, 0.7683692694159514, 0.7683692694159514, 0.7683692694159514, 0.7683692694159514, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7701486288465564, 0.7719279882771615, 0.7719279882771615, 0.7719279882771615, 0.7719279882771615, 0.7719279882771615, 0.7719279882771615, 0.7719279882771615, 0.7719279882771615, 0.7719279882771615, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7772660665689763, 0.7772660665689763, 0.7772660665689763, 0.7772660665689763, 0.7772660665689763, 0.7772660665689763, 0.7772660665689763, 0.7772660665689763, 0.7772660665689763, 0.7772660665689763, 0.7772660665689763, 0.7772660665689763, 0.7772660665689763, 0.7772660665689763, 0.7772660665689763, 0.7772660665689763, 0.7772660665689763, 0.7772660665689763, 0.7772660665689763, 0.7790454259995814, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7808247854301864, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7919719489219175, 0.7919719489219175, 0.7919719489219175, 0.7919719489219175, 0.7919719489219175, 0.7919719489219175, 0.7919719489219175, 0.7919719489219175, 0.7919719489219175, 0.7919719489219175, 0.7919719489219175, 0.7919719489219175, 0.7919719489219175]
tam = [i for i in range(len(io_AGGAC_2))]
fig.add_trace(go.Scatter(y=io_AGGAC_2, x=tam, name='Partición 2', marker = dict(color = 'lightblue')), row=1, col=1)

io_AGGAC_3 = [0.6048252041029936, 0.6048252041029936, 0.6048252041029936, 0.6048252041029936, 0.6048252041029936, 0.6048252041029936, 0.6048252041029936, 0.6048252041029936, 0.6048252041029936, 0.6048252041029936, 0.6048252041029936, 0.6048252041029936, 0.6048252041029936, 0.6048252041029936, 0.6048252041029936, 0.6048252041029936, 0.6066045635335985, 0.6066045635335985, 0.6066045635335985, 0.6066045635335985, 0.6066045635335985, 0.6066045635335985, 0.6066045635335985, 0.6066045635335985, 0.6066045635335985, 0.6066045635335985, 0.6066045635335985, 0.6066045635335985, 0.6066045635335985, 0.6066045635335985, 0.6066045635335985, 0.6066045635335985, 0.6066045635335985, 0.6083839229642035, 0.6083839229642035, 0.6083839229642035, 0.6083839229642035, 0.6083839229642035, 0.6083839229642035, 0.6230898053171446, 0.6230898053171446, 0.6266485241783546, 0.6266485241783546, 0.6266485241783546, 0.6342369688088758, 0.648942851161817, 0.648942851161817, 0.648942851161817, 0.650722210592422, 0.650722210592422, 0.650722210592422, 0.650722210592422, 0.650722210592422, 0.650722210592422, 0.650722210592422, 0.650722210592422, 0.650722210592422, 0.650722210592422, 0.650722210592422, 0.6600900146535482, 0.6600900146535482, 0.6600900146535482, 0.6600900146535482, 0.6600900146535482, 0.6600900146535482, 0.6600900146535482, 0.6672074523759681, 0.6672074523759681, 0.6672074523759681, 0.6672074523759681, 0.6689868118065732, 0.6689868118065732, 0.6765752564370944, 0.6765752564370944, 0.6765752564370944, 0.6765752564370944, 0.6877224199288257, 0.6877224199288257, 0.6877224199288257, 0.6877224199288257, 0.6877224199288257, 0.6877224199288257, 0.6930604982206405, 0.6930604982206405, 0.6930604982206405, 0.6930604982206405, 0.6930604982206405, 0.6930604982206405, 0.6930604982206405, 0.6930604982206405, 0.6930604982206405, 0.6930604982206405, 0.6930604982206405, 0.6930604982206405, 0.6930604982206405, 0.6930604982206405, 0.6930604982206405, 0.6930604982206405, 0.6930604982206405, 0.6930604982206405, 0.6930604982206405, 0.6930604982206405, 0.6930604982206405, 0.6930604982206405, 0.6930604982206405, 0.6930604982206405, 0.6948398576512456, 0.6948398576512456, 0.6948398576512456, 0.6948398576512456, 0.6948398576512456, 0.6948398576512456, 0.6948398576512456, 0.6983985765124555, 0.7077663805735818, 0.7077663805735818, 0.7095457400041867, 0.7095457400041867, 0.7095457400041867, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7131044588653968, 0.7131044588653968, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7313690600795478, 0.7313690600795478, 0.7331484195101527, 0.7331484195101527, 0.7349277789407578, 0.7349277789407578, 0.7349277789407578, 0.7349277789407578, 0.7349277789407578, 0.747854301863094, 0.747854301863094, 0.747854301863094, 0.747854301863094, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7607808247854302, 0.7607808247854302, 0.7607808247854302, 0.7607808247854302, 0.7719279882771615, 0.7719279882771615, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7772660665689763, 0.7772660665689763, 0.7772660665689763, 0.7772660665689763, 0.7772660665689763, 0.7790454259995814, 0.7790454259995814, 0.7790454259995814, 0.7790454259995814, 0.7808247854301864, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7955306677831275, 0.7973100272137326, 0.7990893866443375, 0.7990893866443375, 0.7990893866443375, 0.8008687460749424, 0.8008687460749424, 0.8008687460749424, 0.8008687460749424, 0.8008687460749424, 0.8008687460749424, 0.8008687460749424, 0.8008687460749424, 0.8008687460749424, 0.8008687460749424, 0.8008687460749424, 0.8008687460749424, 0.8008687460749424, 0.8008687460749424, 0.8102365501360687, 0.8102365501360687, 0.8102365501360687, 0.8102365501360687, 0.8102365501360687, 0.8102365501360687, 0.8102365501360687, 0.8102365501360687, 0.8102365501360687, 0.8102365501360687]
tam = [i for i in range(len(io_AGGAC_3))]
fig.add_trace(go.Scatter(y=io_AGGAC_3, x=tam, name='Partición 3', marker = dict(color = 'lightblue')), row=1, col=1)

io_AGGAC_4 = [0.6030458446723885, 0.6030458446723885, 0.6030458446723885, 0.6213104458865397, 0.6213104458865397, 0.6213104458865397, 0.6213104458865397, 0.6213104458865397, 0.6213104458865397, 0.6213104458865397, 0.6213104458865397, 0.6213104458865397, 0.6213104458865397, 0.6213104458865397, 0.6306782499476659, 0.6342369688088758, 0.6342369688088758, 0.6342369688088758, 0.6360163282394808, 0.6360163282394808, 0.6360163282394808, 0.6360163282394808, 0.6360163282394808, 0.6360163282394808, 0.6360163282394808, 0.6360163282394808, 0.6360163282394808, 0.6360163282394808, 0.6360163282394808, 0.6360163282394808, 0.6377956876700859, 0.6377956876700859, 0.6377956876700859, 0.6377956876700859, 0.6377956876700859, 0.6377956876700859, 0.6377956876700859, 0.650722210592422, 0.650722210592422, 0.650722210592422, 0.652501570023027, 0.652501570023027, 0.652501570023027, 0.6618693740841533, 0.6618693740841533, 0.6636487335147583, 0.6636487335147583, 0.6636487335147583, 0.6636487335147583, 0.6636487335147583, 0.6636487335147583, 0.6636487335147583, 0.6636487335147583, 0.6636487335147583, 0.6636487335147583, 0.6636487335147583, 0.6636487335147583, 0.6636487335147583, 0.6636487335147583, 0.6636487335147583, 0.6636487335147583, 0.6636487335147583, 0.6636487335147583, 0.6636487335147583, 0.6654280929453632, 0.6654280929453632, 0.6654280929453632, 0.6672074523759681, 0.6672074523759681, 0.6672074523759681, 0.6672074523759681, 0.6689868118065732, 0.6689868118065732, 0.6689868118065732, 0.6689868118065732, 0.6689868118065732, 0.6689868118065732, 0.6689868118065732, 0.6689868118065732, 0.6689868118065732, 0.6689868118065732, 0.6689868118065732, 0.6689868118065732, 0.6689868118065732, 0.6689868118065732, 0.6689868118065732, 0.6689868118065732, 0.6689868118065732, 0.6689868118065732, 0.6689868118065732, 0.6689868118065732, 0.6689868118065732, 0.6689868118065732, 0.6783546158676994, 0.6783546158676994, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6948398576512456, 0.6948398576512456, 0.6948398576512456, 0.6948398576512456, 0.6948398576512456, 0.6948398576512456, 0.6948398576512456, 0.6948398576512456, 0.6948398576512456, 0.6948398576512456, 0.6948398576512456, 0.6948398576512456, 0.6948398576512456, 0.6948398576512456, 0.6948398576512456, 0.6948398576512456, 0.6948398576512456, 0.6948398576512456, 0.6948398576512456, 0.6948398576512456, 0.6948398576512456, 0.6966192170818506, 0.6966192170818506, 0.6983985765124555, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7166631777266066, 0.7166631777266066, 0.7166631777266066, 0.7166631777266066, 0.7166631777266066, 0.7166631777266066, 0.7166631777266066, 0.7166631777266066, 0.7166631777266066, 0.7166631777266066, 0.7166631777266066, 0.7166631777266066, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7331484195101527, 0.7331484195101527, 0.7331484195101527, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.7460749424324891, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7590014653548252, 0.7607808247854302, 0.7607808247854302, 0.7607808247854302, 0.7607808247854302, 0.7607808247854302, 0.7607808247854302, 0.7607808247854302, 0.7643395436466401, 0.7643395436466401, 0.7643395436466401, 0.7643395436466401, 0.7643395436466401, 0.7643395436466401, 0.7772660665689763, 0.7772660665689763, 0.7772660665689763, 0.7772660665689763, 0.7772660665689763, 0.7772660665689763, 0.7772660665689763, 0.7772660665689763, 0.7772660665689763, 0.7772660665689763, 0.7772660665689763, 0.7772660665689763, 0.7772660665689763, 0.7772660665689763, 0.7772660665689763, 0.7772660665689763, 0.7772660665689763, 0.7790454259995814, 0.7790454259995814, 0.7790454259995814, 0.7790454259995814, 0.7790454259995814, 0.7790454259995814, 0.7790454259995814, 0.7790454259995814, 0.7790454259995814, 0.7790454259995814, 0.7790454259995814, 0.7790454259995814, 0.7790454259995814, 0.7790454259995814, 0.7790454259995814, 0.7790454259995814, 0.7790454259995814, 0.7790454259995814, 0.7790454259995814, 0.7790454259995814, 0.7790454259995814, 0.7790454259995814, 0.7790454259995814, 0.7790454259995814, 0.7790454259995814, 0.7790454259995814, 0.7790454259995814, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7826041448607913, 0.7843835042913962, 0.7843835042913962, 0.7843835042913962, 0.7843835042913962, 0.7843835042913962, 0.7843835042913962, 0.7843835042913962, 0.7843835042913962, 0.7843835042913962, 0.7843835042913962, 0.7843835042913962, 0.7843835042913962, 0.7843835042913962, 0.7843835042913962, 0.7843835042913962, 0.7843835042913962, 0.7843835042913962, 0.7843835042913962]
tam = [i for i in range(len(io_AGGAC_4))]
fig.add_trace(go.Scatter(y=io_AGGAC_4, x=tam, name='Partición 4', marker = dict(color = 'lightblue')), row=1, col=1)

io_AGGAC_5 = [0.5994871258111786, 0.5994871258111786, 0.5994871258111786, 0.5994871258111786, 0.5994871258111786, 0.5994871258111786, 0.5994871258111786, 0.5994871258111786, 0.5994871258111786, 0.5994871258111786, 0.5994871258111786, 0.5994871258111786, 0.5994871258111786, 0.5994871258111786, 0.5994871258111786, 0.5994871258111786, 0.5994871258111786, 0.5994871258111786, 0.5994871258111786, 0.6030458446723885, 0.6030458446723885, 0.6030458446723885, 0.6030458446723885, 0.6030458446723885, 0.6030458446723885, 0.6030458446723885, 0.6030458446723885, 0.6030458446723885, 0.6030458446723885, 0.6177517270253298, 0.6177517270253298, 0.6177517270253298, 0.6177517270253298, 0.6177517270253298, 0.6177517270253298, 0.6177517270253298, 0.6177517270253298, 0.6177517270253298, 0.6177517270253298, 0.6177517270253298, 0.6177517270253298, 0.6177517270253298, 0.6177517270253298, 0.6177517270253298, 0.6177517270253298, 0.6177517270253298, 0.6177517270253298, 0.6177517270253298, 0.6195310864559347, 0.6230898053171446, 0.6230898053171446, 0.6324576093782709, 0.6324576093782709, 0.6324576093782709, 0.6324576093782709, 0.6324576093782709, 0.6324576093782709, 0.6324576093782709, 0.6324576093782709, 0.6324576093782709, 0.6324576093782709, 0.6324576093782709, 0.6324576093782709, 0.6324576093782709, 0.6382666945781872, 0.6382666945781872, 0.6382666945781872, 0.6382666945781872, 0.6382666945781872, 0.6382666945781872, 0.6382666945781872, 0.6382666945781872, 0.6382666945781872, 0.6382666945781872, 0.6382666945781872, 0.6382666945781872, 0.6382666945781872, 0.6382666945781872, 0.6382666945781872, 0.6382666945781872, 0.6382666945781872, 0.6382666945781872, 0.6382666945781872, 0.6382666945781872, 0.6382666945781872, 0.6382666945781872, 0.6382666945781872, 0.6382666945781872, 0.6382666945781872, 0.641825413439397, 0.6436047728700021, 0.6436047728700021, 0.6436047728700021, 0.6436047728700021, 0.6436047728700021, 0.6436047728700021, 0.6436047728700021, 0.6436047728700021, 0.652501570023027, 0.652501570023027, 0.652501570023027, 0.652501570023027, 0.652501570023027, 0.652501570023027, 0.652501570023027, 0.654280929453632, 0.654280929453632, 0.654280929453632, 0.6600900146535482, 0.6636487335147583, 0.6636487335147583, 0.6636487335147583, 0.6636487335147583, 0.6636487335147583, 0.6636487335147583, 0.6636487335147583, 0.6654280929453632, 0.6689868118065732, 0.6689868118065732, 0.6747958970064893, 0.6747958970064893, 0.6747958970064893, 0.6747958970064893, 0.6747958970064893, 0.6747958970064893, 0.6747958970064893, 0.6783546158676994, 0.6783546158676994, 0.6836926941595143, 0.6836926941595143, 0.6836926941595143, 0.6836926941595143, 0.6930604982206405, 0.6930604982206405, 0.6948398576512456, 0.6948398576512456, 0.6948398576512456, 0.6948398576512456, 0.6948398576512456, 0.6948398576512456, 0.6948398576512456, 0.6948398576512456, 0.6948398576512456, 0.6948398576512456, 0.6948398576512456, 0.6966192170818506, 0.6966192170818506, 0.6966192170818506, 0.6966192170818506, 0.6966192170818506, 0.6966192170818506, 0.6966192170818506, 0.6966192170818506, 0.6966192170818506, 0.6966192170818506, 0.6966192170818506, 0.6966192170818506, 0.6966192170818506, 0.6966192170818506, 0.6966192170818506, 0.6966192170818506, 0.6966192170818506, 0.6966192170818506, 0.6966192170818506, 0.7095457400041867, 0.7095457400041867, 0.7095457400041867, 0.7095457400041867, 0.7095457400041867, 0.7095457400041867, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7113250994347917, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7242516223571279, 0.7242516223571279, 0.7242516223571279, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7278103412183379, 0.7278103412183379, 0.7278103412183379, 0.7278103412183379, 0.7278103412183379, 0.7278103412183379, 0.7278103412183379, 0.7278103412183379, 0.7278103412183379, 0.7278103412183379, 0.7278103412183379, 0.7278103412183379, 0.7278103412183379, 0.7278103412183379, 0.7278103412183379, 0.7278103412183379, 0.7278103412183379, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7295897006489429, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692]
tam = [i for i in range(len(io_AGGAC_5))]
fig.add_trace(go.Scatter(y=io_AGGAC_5, x=tam, name='Partición 5', marker = dict(color = 'lightblue')), row=1, col=1)

particiones = [io_AGGAC_1, io_AGGAC_2, io_AGGAC_3, io_AGGAC_4, io_AGGAC_5]
min_len = np.min([len(io_AGGAC_1), len(io_AGGAC_2), len(io_AGGAC_3), len(io_AGGAC_4), len(io_AGGAC_5)])
r = range(min_len)
promedio_AGGAC = []
for i in r: 
    suma = 0
    for p in particiones: 
        suma += p[i]
    promedio_AGGAC.append(suma/5)
tam_promedio_AGGAC = [i for i in range(len(promedio_AGGAC))]
fig.add_trace(go.Scatter(y=promedio_AGGAC, x=tam_promedio_AGGAC, name='Promedio', marker = dict(color = 'red')), row=1, col=1)

# ============== AGGBLX ===================

io_AGGBLX_1 = [0.6523109243697479, 0.6821428571428572, 0.6821428571428572, 0.6821428571428572, 0.6821428571428572, 0.6821428571428572, 0.6942226890756302, 0.6964285714285714, 0.6964285714285714, 0.6964285714285714, 0.6964285714285714, 0.6964285714285714, 0.6964285714285714, 0.6964285714285714, 0.6964285714285714, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7521008403361344, 0.7521008403361344, 0.7521008403361344, 0.7521008403361344, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058, 0.7610294117647058]
tam = [i for i in range(len(io_AGGBLX_1))]
fig.add_trace(go.Scatter(y=io_AGGBLX_1, x=tam, name='Partición 1', marker = dict(color = 'lightblue')), row=1, col=2)

io_AGGBLX_2 = [0.6930604982206405, 0.7131044588653968, 0.7131044588653968, 0.7131044588653968, 0.7131044588653968, 0.7131044588653968, 0.7131044588653968, 0.7131044588653968, 0.7131044588653968, 0.7131044588653968, 0.7131044588653968, 0.7131044588653968, 0.7131044588653968, 0.7131044588653968, 0.7131044588653968, 0.7131044588653968, 0.7131044588653968, 0.7131044588653968, 0.7131044588653968, 0.7131044588653968, 0.722472262926523, 0.722472262926523, 0.722472262926523, 0.722472262926523, 0.722472262926523, 0.722472262926523, 0.722472262926523, 0.722472262926523, 0.722472262926523, 0.722472262926523, 0.722472262926523, 0.722472262926523, 0.722472262926523, 0.722472262926523, 0.722472262926523, 0.722472262926523, 0.722472262926523, 0.722472262926523, 0.722472262926523, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7260309817877328, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7313690600795478, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352, 0.7625601842160352]
tam = [i for i in range(len(io_AGGBLX_2))]
fig.add_trace(go.Scatter(y=io_AGGBLX_2, x=tam, name='Partición 2', marker = dict(color = 'lightblue')), row=1, col=2)

io_AGGBLX_3 = [0.6725455306677831, 0.6801339752983044, 0.6801339752983044, 0.6801339752983044, 0.7131044588653968, 0.7131044588653968, 0.7131044588653968, 0.7131044588653968, 0.7131044588653968, 0.7131044588653968, 0.7131044588653968, 0.7131044588653968, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7291186937408416, 0.7313690600795478, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153, 0.7554427464936153]
tam = [i for i in range(len(io_AGGBLX_3))]
fig.add_trace(go.Scatter(y=io_AGGBLX_3, x=tam, name='Partición 3', marker = dict(color = 'lightblue')), row=1, col=2)

io_AGGBLX_4 = [0.6623403809922546, 0.6806049822064058, 0.6806049822064058, 0.715354825204103, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7171341846347079, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7318400669876491, 0.7336194264182541, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7465459493405904, 0.7483253087711953, 0.7483253087711953, 0.7483253087711953, 0.7483253087711953, 0.7483253087711953, 0.7483253087711953, 0.7483253087711953, 0.7518840276324052, 0.7518840276324052, 0.7518840276324052, 0.7518840276324052, 0.7518840276324052, 0.7518840276324052, 0.7518840276324052, 0.7518840276324052, 0.7518840276324052, 0.7518840276324052, 0.7518840276324052, 0.7518840276324052, 0.7518840276324052, 0.7536633870630103, 0.7536633870630103, 0.7536633870630103, 0.7536633870630103, 0.7536633870630103, 0.7536633870630103, 0.7536633870630103, 0.7536633870630103, 0.7536633870630103, 0.7536633870630103, 0.7536633870630103, 0.7536633870630103, 0.7536633870630103, 0.7536633870630103, 0.7536633870630103, 0.7536633870630103, 0.7536633870630103, 0.7536633870630103, 0.7536633870630103, 0.7536633870630103, 0.7536633870630103, 0.7536633870630103]
tam = [i for i in range(len(io_AGGBLX_4))]
fig.add_trace(go.Scatter(y=io_AGGBLX_4, x=tam, name='Partición 4', marker = dict(color = 'lightblue')), row=1, col=2)

io_AGGBLX_5 = [0.6600900146535482, 0.6730165375758844, 0.6730165375758844, 0.6730165375758844, 0.6877224199288257, 0.6877224199288257, 0.6877224199288257, 0.6877224199288257, 0.6877224199288257, 0.6877224199288257, 0.6877224199288257, 0.6877224199288257, 0.6953108645593469, 0.6953108645593469, 0.6953108645593469, 0.6953108645593469, 0.6953108645593469, 0.6953108645593469, 0.6953108645593469, 0.6953108645593469, 0.7024283022817668, 0.7024283022817668, 0.7024283022817668, 0.7024283022817668, 0.7024283022817668, 0.7024283022817668, 0.7024283022817668, 0.7024283022817668, 0.7024283022817668, 0.7024283022817668, 0.7024283022817668, 0.7024283022817668, 0.7024283022817668, 0.7042076617123718, 0.7042076617123718, 0.7042076617123718, 0.7042076617123718, 0.7042076617123718, 0.7042076617123718, 0.7042076617123718, 0.7042076617123718, 0.7042076617123718, 0.7042076617123718, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7336194264182541, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166, 0.7559137534017166]
tam = [i for i in range(len(io_AGGBLX_5))]
fig.add_trace(go.Scatter(y=io_AGGBLX_5, x=tam, name='Partición 5', marker = dict(color = 'lightblue')), row=1, col=2)

particiones = [io_AGGBLX_1, io_AGGBLX_2, io_AGGBLX_3, io_AGGBLX_4, io_AGGBLX_5]
min_len = np.min([len(io_AGGBLX_1), len(io_AGGBLX_2), len(io_AGGBLX_3), len(io_AGGBLX_4), len(io_AGGBLX_5)])
r = range(min_len)
promedio_AGGBLX = []
for i in r: 
    suma = 0
    for p in particiones: 
        suma += p[i]
    promedio_AGGBLX.append(suma/5)
tam_promedio_AGGBLX = [i for i in range(len(promedio_AGGBLX))]
fig.add_trace(go.Scatter(y=promedio_AGGBLX, x=tam_promedio_AGGBLX, name='Promedio', marker = dict(color = 'red')), row=1, col=2)

# General Styling
fig.update_layout(height=700, bargap=0.2,
                  margin=dict(b=50,r=30,l=100, t=140),
                  plot_bgcolor='rgb(242,242,242)',
                  #paper_bgcolor = 'rgb(242,242,242)',
                  font=dict(family="Times New Roman", size= 14),
                  hoverlabel=dict(font_color="floralwhite"),
                  showlegend=False)

#Title
text = [
    "<span style='font-size:35px; font-family:Times New Roman'>Análisis de convergencia</span>"
]
annotation_helper(fig, text, -0.043, 1.265, [0.095,0.095,0.065],ref="paper", width=1300)
text = [
        "<span style='font-size:14px; font-family:Helvetica'> Convergencia de la función objetivo, para cada uno de los algoritmos <b>genéticos</b>. Hemos usado los resultados obtenidos en el dataset Ionosphere, para cada una de las particiones.</span>",
        "<span style='font-size:14px; font-family:Helvetica'> En color azul claro pueden verse cada una de las particiones. Por su parte, la línea roja representa el valor promedio.</span>",
]
annotation_helper(fig, text, -0.043, 1.175, [0.04,0.095,0.055],ref="paper", width=1300)

fig.show()

In [14]:
fig = make_subplots(rows=1, cols=3, column_widths=[0.33, 0.34, 0.33], horizontal_spacing=0.1,
                    subplot_titles=('AM1','AM2','AM3'))

# ============== AM1 ===================

io_AM1_1 = [0.695063025210084, 0.695063025210084, 0.695063025210084, 0.695063025210084, 0.695063025210084, 0.695063025210084, 0.695063025210084, 0.695063025210084, 0.695063025210084, 0.7454831932773109, 0.7454831932773109, 0.7454831932773109, 0.7454831932773109, 0.7454831932773109, 0.7454831932773109, 0.7454831932773109, 0.7454831932773109, 0.7454831932773109, 0.7454831932773109, 0.773109243697479, 0.773109243697479, 0.773109243697479, 0.773109243697479, 0.773109243697479, 0.773109243697479, 0.773109243697479, 0.773109243697479, 0.773109243697479, 0.773109243697479, 0.7802521008403361, 0.7802521008403361, 0.7802521008403361, 0.7802521008403361, 0.7802521008403361, 0.7802521008403361, 0.7802521008403361, 0.7802521008403361, 0.7802521008403361, 0.7802521008403361, 0.8390756302521009, 0.8390756302521009, 0.8390756302521009, 0.8390756302521009, 0.8390756302521009, 0.8390756302521009, 0.8390756302521009, 0.8390756302521009, 0.8390756302521009, 0.8390756302521009, 0.8484243697478991, 0.8484243697478991, 0.8484243697478991, 0.8484243697478991, 0.8484243697478991, 0.8484243697478991, 0.8484243697478991, 0.8484243697478991, 0.8484243697478991, 0.8484243697478991, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8631302521008404, 0.8631302521008404, 0.8631302521008404, 0.8631302521008404, 0.8631302521008404, 0.8631302521008404, 0.8631302521008404, 0.8631302521008404, 0.8631302521008404, 0.8631302521008404, 0.8649159663865547, 0.8649159663865547, 0.8649159663865547, 0.8649159663865547, 0.8649159663865547, 0.8649159663865547, 0.8649159663865547, 0.8649159663865547, 0.8649159663865547, 0.8649159663865547, 0.8649159663865547, 0.8649159663865547, 0.8649159663865547, 0.8649159663865547, 0.8649159663865547, 0.8649159663865547, 0.8649159663865547, 0.8649159663865547, 0.8649159663865547, 0.8649159663865547, 0.8649159663865547, 0.8649159663865547, 0.8649159663865547, 0.8649159663865547, 0.8649159663865547, 0.8649159663865547, 0.8649159663865547, 0.8649159663865547, 0.8649159663865547, 0.8649159663865547, 0.8667016806722689, 0.8667016806722689, 0.8667016806722689, 0.8667016806722689, 0.8667016806722689, 0.8667016806722689, 0.8667016806722689, 0.8667016806722689, 0.8667016806722689, 0.8667016806722689, 0.8667016806722689, 0.8667016806722689, 0.8667016806722689, 0.8667016806722689, 0.8667016806722689, 0.8667016806722689, 0.8667016806722689, 0.8667016806722689, 0.8667016806722689, 0.8667016806722689, 0.8667016806722689, 0.8667016806722689, 0.8667016806722689, 0.8667016806722689, 0.8667016806722689, 0.8667016806722689, 0.8667016806722689, 0.8667016806722689, 0.8667016806722689, 0.8667016806722689, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244, 0.8706932773109244]
tam = [i for i in range(len(io_AM1_1))]
fig.add_trace(go.Scatter(y=io_AM1_1, x=tam, name='Partición 1', marker = dict(color = 'lightblue')), row=1, col=1)

io_AM1_2 = [0.6484718442537157, 0.6484718442537157, 0.6636487335147583, 0.6801339752983044, 0.6801339752983044, 0.6801339752983044, 0.6801339752983044, 0.6801339752983044, 0.6801339752983044, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.8031191124136488, 0.8031191124136488, 0.8031191124136488, 0.8031191124136488, 0.8031191124136488, 0.8031191124136488, 0.8031191124136488, 0.8031191124136488, 0.8031191124136488, 0.8031191124136488, 0.8066778312748587, 0.8066778312748587, 0.8066778312748587, 0.8066778312748587, 0.8066778312748587, 0.8066778312748587, 0.8066778312748587, 0.8066778312748587, 0.8066778312748587, 0.8066778312748587, 0.8530458446723885, 0.8530458446723885, 0.8530458446723885, 0.8530458446723885, 0.8530458446723885, 0.8530458446723885, 0.8530458446723885, 0.8530458446723885, 0.8530458446723885, 0.8530458446723885, 0.8566045635335985, 0.8566045635335985, 0.8566045635335985, 0.8566045635335985, 0.8566045635335985, 0.8566045635335985, 0.8566045635335985, 0.8566045635335985, 0.8566045635335985, 0.8566045635335985, 0.8566045635335985, 0.8566045635335985, 0.8566045635335985, 0.8566045635335985, 0.8566045635335985, 0.8566045635335985, 0.8566045635335985, 0.8566045635335985, 0.8566045635335985, 0.8566045635335985, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8677517270253297, 0.8677517270253297, 0.8677517270253297, 0.8677517270253297, 0.8677517270253297, 0.8677517270253297, 0.8677517270253297, 0.8677517270253297, 0.8677517270253297, 0.8677517270253297, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8913544065312957, 0.8913544065312957, 0.8913544065312957, 0.8913544065312957, 0.8913544065312957, 0.8913544065312957, 0.8913544065312957, 0.8913544065312957, 0.8913544065312957, 0.8913544065312957, 0.906060288884237, 0.906060288884237, 0.906060288884237, 0.906060288884237, 0.906060288884237, 0.906060288884237, 0.906060288884237, 0.906060288884237, 0.906060288884237, 0.906060288884237, 0.9238538831902867, 0.9238538831902867, 0.9238538831902867, 0.9238538831902867, 0.9238538831902867, 0.9238538831902867, 0.9238538831902867, 0.9238538831902867, 0.9238538831902867, 0.9238538831902867, 0.938559765543228, 0.938559765543228, 0.938559765543228, 0.938559765543228, 0.938559765543228, 0.938559765543228, 0.938559765543228, 0.938559765543228, 0.938559765543228, 0.938559765543228, 0.9403391249738329, 0.9403391249738329, 0.9403391249738329, 0.9403391249738329, 0.9403391249738329, 0.9403391249738329, 0.9403391249738329, 0.9403391249738329, 0.9403391249738329, 0.9403391249738329, 0.9403391249738329, 0.9403391249738329, 0.9403391249738329, 0.9403391249738329, 0.9403391249738329, 0.9403391249738329, 0.9403391249738329, 0.9403391249738329, 0.9403391249738329, 0.9403391249738329, 0.9403391249738329]
tam = [i for i in range(len(io_AM1_2))]
fig.add_trace(go.Scatter(y=io_AM1_2, x=tam, name='Partición 2', marker = dict(color = 'lightblue')), row=1, col=1)

io_AM1_3 = [0.6453841323006071, 0.6453841323006071, 0.6654280929453632, 0.7001779359430604, 0.7001779359430604, 0.7001779359430604, 0.7001779359430604, 0.7001779359430604, 0.7001779359430604, 0.7367071383713628, 0.7367071383713628, 0.7367071383713628, 0.7367071383713628, 0.7367071383713628, 0.7367071383713628, 0.7367071383713628, 0.7367071383713628, 0.7367071383713628, 0.7367071383713628, 0.7790454259995814, 0.7790454259995814, 0.7790454259995814, 0.7790454259995814, 0.7790454259995814, 0.7790454259995814, 0.7790454259995814, 0.7790454259995814, 0.7790454259995814, 0.7790454259995814, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.8356185890726398, 0.8356185890726398, 0.8356185890726398, 0.8356185890726398, 0.8356185890726398, 0.8356185890726398, 0.8356185890726398, 0.8356185890726398, 0.8356185890726398, 0.8356185890726398, 0.8356185890726398, 0.8356185890726398, 0.8356185890726398, 0.8356185890726398, 0.8356185890726398, 0.8356185890726398, 0.8356185890726398, 0.8356185890726398, 0.8356185890726398, 0.8356185890726398, 0.8356185890726398, 0.8356185890726398, 0.8356185890726398, 0.8356185890726398, 0.8356185890726398, 0.8356185890726398, 0.8356185890726398, 0.8356185890726398, 0.8356185890726398, 0.8356185890726398, 0.8503244714255809, 0.8503244714255809, 0.8503244714255809, 0.8521038308561859, 0.8521038308561859, 0.8521038308561859, 0.8521038308561859, 0.8521038308561859, 0.8521038308561859, 0.8521038308561859, 0.8797362361314632, 0.8797362361314632, 0.8797362361314632, 0.8797362361314632, 0.8797362361314632, 0.8797362361314632, 0.8797362361314632, 0.8797362361314632, 0.8797362361314632, 0.8797362361314632, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732, 0.8832949549926732]
tam = [i for i in range(len(io_AM1_3))]
fig.add_trace(go.Scatter(y=io_AM1_3, x=tam, name='Partición 3', marker = dict(color = 'lightblue')), row=1, col=1)

io_AM1_4 = [0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.6819133347289094, 0.688193426836927, 0.688193426836927, 0.688193426836927, 0.688193426836927, 0.688193426836927, 0.7572221059242202, 0.7572221059242202, 0.7572221059242202, 0.7572221059242202, 0.7572221059242202, 0.7572221059242202, 0.7572221059242202, 0.7572221059242202, 0.7572221059242202, 0.7572221059242202, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.7665899099853465, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.81070755704417, 0.81070755704417, 0.81070755704417, 0.81070755704417, 0.81070755704417, 0.81070755704417, 0.81070755704417, 0.81070755704417, 0.81070755704417, 0.81070755704417, 0.8289721582583212, 0.8289721582583212, 0.8289721582583212, 0.8289721582583212, 0.8289721582583212, 0.8289721582583212, 0.8289721582583212, 0.8289721582583212, 0.8289721582583212, 0.8289721582583212, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136]
tam = [i for i in range(len(io_AM1_4))]
fig.add_trace(go.Scatter(y=io_AM1_4, x=tam, name='Partición 4', marker = dict(color = 'lightblue')), row=1, col=1)

io_AM1_5 = [0.5941490475193636, 0.6676784592840694, 0.6676784592840694, 0.6676784592840694, 0.6676784592840694, 0.6676784592840694, 0.6676784592840694, 0.7340904333263555, 0.7340904333263555, 0.7706196357546578, 0.7706196357546578, 0.7706196357546578, 0.7706196357546578, 0.7706196357546578, 0.7706196357546578, 0.7706196357546578, 0.7706196357546578, 0.7706196357546578, 0.7706196357546578, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.808928197613565, 0.81426627590538, 0.81426627590538, 0.81426627590538, 0.81426627590538, 0.81426627590538, 0.81426627590538, 0.81426627590538, 0.81426627590538, 0.81426627590538, 0.81426627590538, 0.8454574000418673, 0.8454574000418673, 0.8454574000418673, 0.8454574000418673, 0.8454574000418673, 0.8454574000418673, 0.8454574000418673, 0.8454574000418673, 0.8454574000418673, 0.8454574000418673, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8566045635335985, 0.8566045635335985, 0.8566045635335985, 0.8566045635335985, 0.8566045635335985, 0.8566045635335985, 0.8566045635335985, 0.8566045635335985, 0.8566045635335985, 0.8566045635335985, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8655013606866233, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695]
tam = [i for i in range(len(io_AM1_5))]
fig.add_trace(go.Scatter(y=io_AM1_5, x=tam, name='Partición 5', marker = dict(color = 'lightblue')), row=1, col=1)

particiones = [io_AM1_1, io_AM1_2, io_AM1_3, io_AM1_4, io_AM1_5]
min_len = np.min([len(io_AM1_1), len(io_AM1_2), len(io_AM1_3), len(io_AM1_4), len(io_AM1_5)])
r = range(min_len)
promedio_AM1 = []
for i in r: 
    suma = 0
    for p in particiones: 
        suma += p[i]
    promedio_AM1.append(suma/5)
tam_promedio_AM1 = [i for i in range(len(promedio_AM1))]
fig.add_trace(go.Scatter(y=promedio_AM1, x=tam_promedio_AM1, name='Promedio', marker = dict(color = 'red')), row=1, col=1)


# ================= AM2 =====================0
io_AM2_1 = [0.659453781512605, 0.659453781512605, 0.659453781512605, 0.659453781512605, 0.659453781512605, 0.659453781512605, 0.659453781512605, 0.659453781512605, 0.6741596638655463, 0.679936974789916, 0.679936974789916, 0.679936974789916, 0.679936974789916, 0.679936974789916, 0.679936974789916, 0.679936974789916, 0.679936974789916, 0.6817226890756303, 0.6817226890756303, 0.6817226890756303, 0.6817226890756303, 0.6817226890756303, 0.6817226890756303, 0.6817226890756303, 0.6817226890756303, 0.6817226890756303, 0.6817226890756303, 0.6817226890756303, 0.6817226890756303, 0.6817226890756303, 0.6817226890756303, 0.7022058823529411, 0.7022058823529411, 0.7022058823529411, 0.7022058823529411, 0.7022058823529411, 0.7022058823529411, 0.7022058823529411, 0.7022058823529411, 0.7129201680672269, 0.7129201680672269, 0.7129201680672269, 0.7129201680672269, 0.7129201680672269, 0.7129201680672269, 0.7129201680672269, 0.7129201680672269, 0.7129201680672269, 0.7129201680672269, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7387605042016807, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345, 0.7771008403361345]
tam = [i for i in range(len(io_AM2_1))]
fig.add_trace(go.Scatter(y=io_AM2_1, x=tam, name='Partición 1', marker = dict(color = 'lightblue')), row=1, col=2)

io_AM2_2 = [0.652501570023027, 0.6613983671760519, 0.7059870211429768, 0.7059870211429768, 0.7059870211429768, 0.7059870211429768, 0.7059870211429768, 0.7059870211429768, 0.7059870211429768, 0.7059870211429768, 0.7059870211429768, 0.7059870211429768, 0.7059870211429768, 0.7059870211429768, 0.7059870211429768, 0.7059870211429768, 0.7059870211429768, 0.7059870211429768, 0.7059870211429768, 0.81070755704417, 0.81070755704417, 0.81070755704417, 0.81070755704417, 0.81070755704417, 0.81070755704417, 0.81070755704417, 0.81070755704417, 0.812486916474775, 0.812486916474775, 0.812486916474775, 0.812486916474775, 0.812486916474775, 0.812486916474775, 0.812486916474775, 0.812486916474775, 0.812486916474775, 0.812486916474775, 0.812486916474775, 0.812486916474775, 0.8561335566254972, 0.8561335566254972, 0.8561335566254972, 0.8561335566254972, 0.8561335566254972, 0.8561335566254972, 0.8561335566254972, 0.8561335566254972, 0.8561335566254972, 0.8561335566254972, 0.8561335566254972, 0.8561335566254972, 0.8561335566254972, 0.8561335566254972, 0.8561335566254972, 0.8561335566254972, 0.8561335566254972, 0.8561335566254972, 0.8561335566254972, 0.8561335566254972, 0.8561335566254972, 0.8561335566254972, 0.8561335566254972, 0.8561335566254972, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8583839229642034, 0.8748691647477496, 0.8748691647477496, 0.8748691647477496, 0.8748691647477496, 0.8748691647477496, 0.8748691647477496, 0.8748691647477496, 0.8748691647477496, 0.8748691647477496, 0.8748691647477496, 0.8748691647477496, 0.8748691647477496, 0.8748691647477496, 0.8748691647477496, 0.8748691647477496, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546, 0.8766485241783546]
tam = [i for i in range(len(io_AM2_2))]
fig.add_trace(go.Scatter(y=io_AM2_2, x=tam, name='Partición 2', marker = dict(color = 'lightblue')), row=1, col=2)

io_AM2_3 = [0.623560812225246, 0.6770462633451957, 0.6770462633451957, 0.6877224199288257, 0.6877224199288257, 0.6877224199288257, 0.6877224199288257, 0.6877224199288257, 0.6877224199288257, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.744295583001884, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7594724722629265, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7630311911241365, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501, 0.7678982625078501]
tam = [i for i in range(len(io_AM2_3))]
fig.add_trace(go.Scatter(y=io_AM2_3, x=tam, name='Partición 3', marker = dict(color = 'lightblue')), row=1, col=2)

io_AM2_4 = [0.6672074523759681, 0.6672074523759681, 0.6672074523759681, 0.6672074523759681, 0.6676784592840694, 0.6676784592840694, 0.6676784592840694, 0.6676784592840694, 0.6676784592840694, 0.6676784592840694, 0.6783546158676994, 0.6783546158676994, 0.6783546158676994, 0.6783546158676994, 0.6783546158676994, 0.6783546158676994, 0.6783546158676994, 0.6783546158676994, 0.6783546158676994, 0.6783546158676994, 0.6783546158676994, 0.6783546158676994, 0.6783546158676994, 0.6783546158676994, 0.6783546158676994, 0.6783546158676994, 0.6819133347289094, 0.6819133347289094, 0.6823843416370107, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7202218965878167, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7371781452794641, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7576931128323215, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251, 0.7946933221687251]
tam = [i for i in range(len(io_AM2_4))]
fig.add_trace(go.Scatter(y=io_AM2_4, x=tam, name='Partición 4', marker = dict(color = 'lightblue')), row=1, col=2)

io_AM2_5 = [0.6712371781452795, 0.6712371781452795, 0.6712371781452795, 0.6712371781452795, 0.6712371781452795, 0.6712371781452795, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7376491521875654, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.7901925894913125, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437, 0.8013397529830437]
tam = [i for i in range(len(io_AM2_5))]
fig.add_trace(go.Scatter(y=io_AM2_5, x=tam, name='Partición 5', marker = dict(color = 'lightblue')), row=1, col=2)

particiones = [io_AM2_1, io_AM2_2, io_AM2_3, io_AM2_4, io_AM2_5]
min_len = np.min([len(io_AM2_1), len(io_AM2_2), len(io_AM2_3), len(io_AM2_4), len(io_AM2_5)])
r = range(min_len)
promedio_AM2 = []
for i in r: 
    suma = 0
    for p in particiones: 
        suma += p[i]
    promedio_AM2.append(suma/5)
tam_promedio_AM2 = [i for i in range(len(promedio_AM2))]
fig.add_trace(go.Scatter(y=promedio_AM2, x=tam_promedio_AM2, name='Promedio', marker = dict(color = 'red')), row=1, col=2)

# ================= AM3 =====================0
io_AM3_1 = [0.6616596638655462, 0.6616596638655462, 0.6616596638655462, 0.6875, 0.6875, 0.6875, 0.6875, 0.6875, 0.6875, 0.7957983193277312, 0.7957983193277312, 0.7957983193277312, 0.7957983193277312, 0.7957983193277312, 0.7957983193277312, 0.7957983193277312, 0.7957983193277312, 0.7957983193277312, 0.7957983193277312, 0.8047268907563025, 0.8047268907563025, 0.8047268907563025, 0.8047268907563025, 0.8047268907563025, 0.8047268907563025, 0.8047268907563025, 0.8047268907563025, 0.8047268907563025, 0.8047268907563025, 0.8065126050420168, 0.8065126050420168, 0.8065126050420168, 0.8065126050420168, 0.8065126050420168, 0.8065126050420168, 0.8065126050420168, 0.8065126050420168, 0.8065126050420168, 0.8065126050420168, 0.8100840336134454, 0.8100840336134454, 0.8100840336134454, 0.8100840336134454, 0.8100840336134454, 0.8100840336134454, 0.8100840336134454, 0.8100840336134454, 0.8100840336134454, 0.8100840336134454, 0.8394957983193276, 0.8394957983193276, 0.8394957983193276, 0.8394957983193276, 0.8394957983193276, 0.8394957983193276, 0.8394957983193276, 0.8394957983193276, 0.8394957983193276, 0.8394957983193276, 0.8412815126050419, 0.8412815126050419, 0.8412815126050419, 0.8412815126050419, 0.8412815126050419, 0.8412815126050419, 0.8412815126050419, 0.8412815126050419, 0.8412815126050419, 0.8412815126050419, 0.8412815126050419, 0.8412815126050419, 0.8412815126050419, 0.8412815126050419, 0.8412815126050419, 0.8412815126050419, 0.8412815126050419, 0.8412815126050419, 0.8412815126050419, 0.8412815126050419, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8595588235294118, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261, 0.8613445378151261]
tam = [i for i in range(len(io_AM3_1))]
fig.add_trace(go.Scatter(y=io_AM3_1, x=tam, name='Partición 1', marker = dict(color = 'lightblue')), row=1, col=3)

io_AM3_2 = [0.6253401716558509, 0.6306782499476659, 0.6613983671760519, 0.6613983671760519, 0.6613983671760519, 0.6983985765124555, 0.6983985765124555, 0.6983985765124555, 0.6983985765124555, 0.720692903495918, 0.720692903495918, 0.720692903495918, 0.720692903495918, 0.720692903495918, 0.720692903495918, 0.720692903495918, 0.720692903495918, 0.720692903495918, 0.720692903495918, 0.7701486288465564, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7737073477077664, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326, 0.7973100272137326] 
tam = [i for i in range(len(io_AM3_2))]
fig.add_trace(go.Scatter(y=io_AM3_2, x=tam, name='Partición 2', marker = dict(color = 'lightblue')), row=1, col=3)

io_AM3_3 = [0.6400460540087921, 0.6672074523759681, 0.6672074523759681, 0.6890307724513293, 0.6890307724513293, 0.6890307724513293, 0.6890307724513293, 0.6890307724513293, 0.6890307724513293, 0.7496336612936989, 0.7496336612936989, 0.7501046682018003, 0.7501046682018003, 0.7501046682018003, 0.7501046682018003, 0.7501046682018003, 0.7501046682018003, 0.7501046682018003, 0.7501046682018003, 0.8231630730584049, 0.8231630730584049, 0.8231630730584049, 0.8231630730584049, 0.8231630730584049, 0.8231630730584049, 0.8231630730584049, 0.8231630730584049, 0.8231630730584049, 0.8231630730584049, 0.832530877119531, 0.832530877119531, 0.832530877119531, 0.832530877119531, 0.832530877119531, 0.832530877119531, 0.832530877119531, 0.832530877119531, 0.832530877119531, 0.832530877119531, 0.8525748377642872, 0.8525748377642872, 0.8525748377642872, 0.8525748377642872, 0.8525748377642872, 0.8525748377642872, 0.8525748377642872, 0.8525748377642872, 0.8525748377642872, 0.8525748377642872, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8802072430395645, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695, 0.8819866024701695]
tam = [i for i in range(len(io_AM3_3))]
fig.add_trace(go.Scatter(y=io_AM3_3, x=tam, name='Partición 3', marker = dict(color = 'lightblue')), row=1, col=3)

io_AM3_4 = [0.6494138580699184, 0.6494138580699184, 0.6494138580699184, 0.6494138580699184, 0.6494138580699184, 0.6494138580699184, 0.6618693740841533, 0.7006489428511617, 0.7006489428511617, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7389575047100692, 0.7754867071383713, 0.7754867071383713, 0.7754867071383713, 0.7754867071383713, 0.7754867071383713, 0.7754867071383713, 0.7754867071383713, 0.7754867071383713, 0.7754867071383713, 0.7754867071383713, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7884132300607076, 0.7977810341218339, 0.7977810341218339, 0.7977810341218339, 0.7977810341218339, 0.7977810341218339, 0.7977810341218339, 0.7977810341218339, 0.7977810341218339, 0.7977810341218339, 0.7977810341218339, 0.8231630730584049, 0.8231630730584049, 0.8231630730584049, 0.8231630730584049, 0.8231630730584049, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.834310236550136, 0.837868955411346, 0.837868955411346, 0.837868955411346, 0.837868955411346, 0.837868955411346, 0.837868955411346, 0.837868955411346, 0.837868955411346, 0.837868955411346, 0.837868955411346, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822, 0.8507954783336822]
tam = [i for i in range(len(io_AM3_4))]
fig.add_trace(go.Scatter(y=io_AM3_4, x=tam, name='Partición 4', marker = dict(color = 'lightblue')), row=1, col=3)

io_AM3_5 = [0.6970902239899519, 0.6970902239899519, 0.6970902239899519, 0.6970902239899519, 0.6970902239899519, 0.6970902239899519, 0.6970902239899519, 0.6970902239899519, 0.6970902239899519, 0.7812957923382877, 0.7812957923382877, 0.7812957923382877, 0.7812957923382877, 0.7812957923382877, 0.7812957923382877, 0.7812957923382877, 0.7812957923382877, 0.7812957923382877, 0.7812957923382877, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949, 0.8196043541971949] 
tam = [i for i in range(len(io_AM3_5))]
fig.add_trace(go.Scatter(y=io_AM3_5, x=tam, name='Partición 5', marker = dict(color = 'lightblue')), row=1, col=3)

particiones = [io_AM3_1, io_AM3_2, io_AM3_3, io_AM3_4, io_AM3_5]
min_len = np.min([len(io_AM3_1), len(io_AM3_2), len(io_AM3_3), len(io_AM3_4), len(io_AM3_5)])
r = range(min_len)
promedio_AM3 = []
for i in r: 
    suma = 0
    for p in particiones: 
        suma += p[i]
    promedio_AM3.append(suma/5)
tam_promedio_AM3 = [i for i in range(len(promedio_AM3))]
fig.add_trace(go.Scatter(y=promedio_AM3, x=tam_promedio_AM3, name='Promedio', marker = dict(color = 'red')), row=1, col=3)

# General Styling
fig.update_layout(height=400, bargap=0.2,
                  margin=dict(b=50,r=30,l=100, t=120),
                  plot_bgcolor='rgb(242,242,242)',
                  #paper_bgcolor = 'rgb(242,242,242)',
                  font=dict(family="Times New Roman", size= 14),
                  hoverlabel=dict(font_color="floralwhite"),
                  showlegend=False)

#Title
text = [
    "<span style='font-size:35px; font-family:Times New Roman'>Análisis de convergencia</span>"
]
annotation_helper(fig, text, -0.043, 1.55, [0.095,0.095,0.065],ref="paper", width=1300)
text = [
        "<span style='font-size:14px; font-family:Helvetica'> Convergencia de la función objetivo, para cada uno de los algoritmos <b>meméticos</b>. Hemos usado los resultados obtenidos en el dataset Ionosphere, para cada una de las particiones.</span>",
        "<span style='font-size:14px; font-family:Helvetica'> En color azul claro pueden verse cada una de las particiones. Por su parte, la línea roja representa el valor promedio.</span>",
]
annotation_helper(fig, text, -0.043, 1.35, [0.065,0.095,0.055],ref="paper", width=1300)

fig.show()

In [8]:
v = []
for i in range(20):
    v.append(i)    
v[:10]

[0, 1, 2, 3, 4, 5, 6, 7, 8, 9]